In [1]:
import pandas as pd
import sys
import os.path
import numpy as np

import bokeh.plotting
from bokeh.plotting import figure, output_server, output_notebook, show, gridplot, reset_output

sys.path.append("/home/daliu/Src/spykshrk_realtime/")

import spykshrk.realtime.binary_record as bin_rec

pd.set_option('float_format', '{:,.1f}'.format)
pd.set_option('display.max_rows', 10)
pd.set_option('display.width', 120)

output_notebook()

Loading BokehJS ...

In [4]:
rec_dir = '/opt/data36/daliu/realtime/spykshrk'
rec_dir = '/home/daliu/output/test'
mpi_ranks = [2, 3]
file_prefix = 'test_animal'
manager_label = 'state'
file_postfix = 'bin_rec'

allrecs = {}

for mpi_rank in mpi_ranks:
    binrec = bin_rec.BinaryRecordsFileReader(save_dir=rec_dir, file_prefix=file_prefix,
                                             mpi_rank=mpi_rank,
                                             manager_label=manager_label,
                                             file_postfix=file_postfix, filemeta_as_col=False)

    rec_pandas = binrec.convert_pandas()
    
    for rec_id, rec_pd in rec_pandas.items():
        existing_rec_pd = allrecs.setdefault(rec_id, pd.DataFrame())
        allrecs[rec_id] = existing_rec_pd.append(rec_pd, ignore_index=True). \
                sort_values(['current_time']).reset_index(drop=True)


In [5]:
ripple_ntrode5 = allrecs[1][allrecs[1]['ntrode_index']==5]

In [6]:
ripple_ntrode5

rec_ind  current_time  ntrode_index thresh_crossed lockout  lfp_data    rd  current_val
0             0      73830243             5           True   False    -117.0  -2.8          0.0
3             1      73830263             5           True   False    -114.0  -9.6          0.6
4             2      73830283             5           True   False    -120.0 -12.1          2.0
6             3      73830303             5           True   False    -141.0   1.3          1.8
8             4      73830323             5           True   False    -125.0  25.3          6.3
...         ...           ...           ...            ...     ...       ...   ...          ...
179967    89983      75629903             5           True   False      -9.0  16.6         12.9
179969    89984      75629923             5           True   False      -5.0  17.3         15.1
179971    89985      75629943             5           True   False       4.0  13.0         14.7
179973    89986      75629963             5           True   False       9.0   1.7         12.1
179974    89987      75629982             5           True   False      11.0 -14.4         13.2

[89988 rows x 8 columns]

In [14]:
s1 = figure(plot_width=900, plot_height=400)
s1.line(x=ripple_ntrode5['current_time']/30000,
       y=ripple_ntrode5['lfp_data'], color='gray')
s1.line(x=ripple_ntrode5['current_time']/30000,
       y=ripple_ntrode5['rd'], color='blue')
s1.line(x=ripple_ntrode5['current_time']/30000,
       y=ripple_ntrode5['current_val'], color='red')


show(s1)